# Model input ERP format preparation 

In this notebook: 
- Necessary inputs
- Read all epochs
- Function to create dataframe with average mismatch response for all participants (needs to be transformed to function)
- Formatting dataframe as suitable model input

## Imports

In [1]:
import mne      # toolbox for analyzing and visualizing EEG data
import os       # using operating system dependent functionality (folders)
import pandas as pd # data analysis and manipulation
import numpy as np    # numerical computing (manipulating and performing operations on arrays of data)
import copy     # Can Copy and Deepcopy files so original file is untouched.
from ipywidgets import IntSlider, Output
import ipywidgets as widgets
from IPython.display import display
import matplotlib.pyplot as plt
from math import nan
from scipy import stats

import sys
sys.path.insert(0, '../eegyolk') # path to helper functions
import helper_functions as hf # library useful for eeg and erp data cleaning
import initialization_functions #library to import data
import epod_helper

In [2]:
metadata = pd.read_csv('metadata.csv', sep = ',')

In [3]:
metadata

eeg_file  ParticipantID test sex  age_months age_months_days  \
0      101a            101    a   m          20           20;22   
1      101b            101    b   m          23           23;16   
2      102a            102    a   f          20           20;27   
3      102b            102    b   f          23           23;16   
4      103a            103    a   f          20           20;23   
..      ...            ...  ...  ..         ...             ...   
57     134a            134    a   m          19           19;20   
58     134b            134    b   m          23            23;7   
59     135a            135    a   f          18           18;21   
60     135b            135    b   f          22            22;8   
61     136a            136    a   f          19           19;11   

   dyslexic_parent Group_AccToParents  \
0                m            At risk   
1                m            At risk   
2              Nee            Control   
3              Nee            Control   
4                m            At risk   
..             ...                ...   
57             Nee            Control   
58             Nee            Control   
59             Nee            Control   
60             Nee            Control   
61             Nee            Control   

                                             eeg_path path_epoch    epoch_file  
0   F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  101a_epo.fif  
1   F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  101b_epo.fif  
2   F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  102a_epo.fif  
3   F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  102b_epo.fif  
4   F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  103a_epo.fif  
..                                                ...        ...           ...  
57  F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  134a_epo.fif  
58  F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  134b_epo.fif  
59  F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  135a_epo.fif  
60  F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  135b_epo.fif  
61  F:\Stage\ePODIUM\Data\ePodium_projectfolder\Da...     epochs  136a_epo.fif  

[62 rows x 11 columns]

## Read all epochs from files

The function below loads all filtered epochs from the dataframe which contains the metadata and the epochs filepaths + filenames. The epochs are arrays for each stimuli with a time interval of -0.3 to 0.7.

In [4]:
def read_filtered_data(metadata):
    epochs = []
    for index, file in metadata.iterrows():
        print(f"Checking out file: {file['epoch_file']}")
        path = os.path.join(file['path_epoch'], file['epoch_file'])
        epoch = mne.read_epochs(path, preload=False)
        epochs.append(epoch)
    return epochs

In [5]:
epochs = read_filtered_data(metadata)

Checking out file: 101a_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\101a_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
2266 matching events found
No baseline correction applied
0 projection items activated
Checking out file: 101b_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\101b_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
2440 matching events found
No baseline correction applied
0 projection items activated
Checking out file: 102a_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\102a_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
2389 matching events found
No baseline correction applied
0 p

Checking out file: 115a_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\115a_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
1220 matching events found
No baseline correction applied
0 projection items activated
Checking out file: 115b_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\115b_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
1220 matching events found
No baseline correction applied
0 projection items activated
Checking out file: 116a_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\116a_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
2266 matching events found
No baseline correction applied
0 p

Checking out file: 129b_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\129b_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
2302 matching events found
No baseline correction applied
0 projection items activated
Checking out file: 130a_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\130a_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
2389 matching events found
No baseline correction applied
0 projection items activated
Checking out file: 130b_epo.fif
Reading F:\Stage\ePODIUM\eegyolk\dyslexiaprediction_nadine\epochs\130b_epo.fif ...
    Found the data of interest:
        t =    -299.80 ...     700.20 ms
        0 CTF compensation matrices available
Not setting metadata
2440 matching events found
No baseline correction applied
0 p

## Create pandas dataframe with the average difference between standard and deviant responses

The function below needs `metadata`, the loaded `epochs` and the definition of the standard and deviant events as input. You should define your standard and deviant events as an array. In the function `input_mmr_prep` it's important to know that the assumption is made that the deviant follows after a standard event. Therefore the deviant belonging to the standard is the  standard event number + 1. Make sure your events are numbered like this, else the function won't calculate the mismatch response.  

In [6]:
# define the events for standard and deviant
standard_events = [2,5,8,11]
deviant_events = [3,6,9,12]

def input_mmr_prep(metadata, epochs, standard_events): 
    # create dataframe with expected columns 
    df = pd.DataFrame(columns=["eeg_file", "paradigm", "channel", "mean"])

    # loop over all participants
    for i in range(len(metadata['eeg_file'])):
        
        # loop over every paradigm per participant 
        for j in standard_events: 
            paradigm = j
            # select the standard and deviant for a specific sequence and calculate the evoked response
            std_evoked = epochs[i][j].average() 
            dev_evoked = epochs[i][j+1].average()
            
            # calculate the mismatch response between standard and deviant evoked
            evoked_diff = mne.combine_evoked([std_evoked, dev_evoked], weights=[1, -1])
            
            # get a list of all channels
            chnames_list = evoked_diff.info['ch_names']
            
            # compute for every channel the distance mean of the mismatch line
            for channel in chnames_list: 
                chnames = mne.pick_channels(evoked_diff.info['ch_names'], include=[channel])
                roi_dict = dict(left_ROI=chnames) # unfortunately combine_channels only takes a dictionary as input
                roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
                mmr = roi_evoked.to_data_frame()
                mmr_avg = mmr['left_ROI'].mean()
                mmr_std = mmr['left_ROI'].std()
                mmr_skew = mmr['left_ROI'].skew()
                mmr_var = mmr['left_ROI'].var()
                mmr_kurt = mmr['left_ROI'].kurtosis()
                
                df = df.append({'eeg_file': metadata['eeg_file'][i], 'paradigm' : paradigm, 'channel': channel, 'mean' :  mmr_avg, 'std' : mmr_std, 'skew' : mmr_skew, 'kurt' : mmr_kurt, 'var' : mmr_var}, ignore_index=True) 
    return df

In [8]:
df = input_mmr_prep(metadata, epochs, standard_events)

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

...

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoked = mne.channels.combine_channels(evoked_diff, roi_dict, method='mean')
<ipython-input-6-60b7c6f8b01a>:29: RuntimeWarning: Less than 2 channels in group "left_ROI" when combining by method "functools.partial(<function mean at 0x00000206556D0B80>, axis=0)".
  roi_evoke

In [9]:
df

eeg_file paradigm channel       mean      kurt      skew        std  \
0        101a        2     Fp1   3.981499 -0.473225 -0.221788  17.493933   
1        101a        2     AF3  11.639081 -0.045013 -0.415601  20.245663   
2        101a        2      F7 -18.811622  0.780759 -0.932338  48.723666   
3        101a        2      F3  18.343454  0.202824 -0.536377  20.851958   
4        101a        2     FC1  10.023632 -0.763461 -0.361099  28.558499   
...       ...      ...     ...        ...       ...       ...        ...   
7931     136a       11      F8 -45.395341 -1.282744 -0.220910  55.436317   
7932     136a       11     AF4 -55.454145 -1.131096 -0.251364  70.113263   
7933     136a       11     Fp2 -48.429236 -1.347975 -0.034679  52.788843   
7934     136a       11      Fz -53.268450 -0.677405 -0.160173  60.994033   
7935     136a       11      Cz -43.441470  0.351654 -0.297694  55.698017   

              var  
0      306.037693  
1      409.886867  
2     2373.995612  
3      434.804153  
4      815.587885  
...           ...  
7931  3073.185281  
7932  4915.869612  
7933  2786.661985  
7934  3720.272119  
7935  3102.269122  

[7936 rows x 8 columns]

## Transpose dataframe into combination of paradigm and channel per participant

We now want a single row for every participant containing the paradigm and corresponding channels. The code below generates this dataframe. 

In [10]:
# transformation of the dataframe
df = df.pivot(index='eeg_file', columns=['paradigm','channel'])
df

mean                                                         \
paradigm         2                                                           
channel         Fp1        AF3         F7         F3        FC1        FC5   
eeg_file                                                                     
101a       3.981499  11.639081 -18.811622  18.343454  10.023632  -4.024143   
101b      -9.964857  -7.810340  19.733811   3.661548  14.292444  32.492531   
102a       2.390371 -17.843979  -3.338771   7.536740 -10.998419  18.220947   
102b       7.074118  23.187111  -9.459183  25.835532  18.345802  34.434200   
103a     -18.065883 -17.785199 -12.858838  -8.709094   9.764843  -1.953743   
...             ...        ...        ...        ...        ...        ...   
134a      25.305783  39.678430  29.960605  22.644373   2.972337  40.967793   
134b      -9.407622  -9.174790 -29.506209 -12.091466  -3.002780 -12.201141   
135a     -24.276921 -15.623758 -40.422530  -1.687877  11.960549 -12.416261   
135b     -18.316388  -1.091161 -33.190223  -7.661494  19.655141   1.925744   
136a     -23.800958   4.628651 -71.338129 -65.563532 -63.851880 -47.764771   

                                                      ...          var  \
paradigm                                              ...           11   
channel          T7         C3        CP1        CP5  ...           C4   
eeg_file                                              ...                
101a     -13.999364 -17.671889 -29.638338 -20.809440  ...  1250.903147   
101b      34.867429  41.204902  33.612812  31.951770  ...   638.018139   
102a      16.625307  -4.156407 -17.935160  -6.441905  ...   968.669479   
102b      34.885866  22.527005  37.353435  30.657794  ...   525.391609   
103a      -2.150446  11.090374   0.289517   2.440453  ...  3465.824136   
...             ...        ...        ...        ...  ...          ...   
134a      15.140849  -5.808729   2.409057   2.371273  ...  1553.391866   
134b     -28.593497   9.314769 -14.475088 -10.563468  ...  1413.633013   
135a       1.713572  26.404282   4.149861   8.584280  ...  1127.357596   
135b       8.144818   4.500359  -0.237321 -28.335054  ...  3136.622465   
136a       1.639489 -45.163899 -48.791706 -30.078101  ...   951.714398   

                                                                           \
paradigm                                                                    
channel            T8          FC6          FC2           F4           F8   
eeg_file                                                                    
101a      1048.163775   829.777806  1753.590043  1872.420561  1177.183239   
101b       265.097401   829.590332   841.305561   998.880934   927.018252   
102a      1071.194015  1716.894816   715.093446  1024.329442   481.196607   
102b      1310.806211  1220.034698   699.721095   640.816934  1312.299428   
103a      4562.069804  3921.895014  4897.122661  6606.174032  5596.697825   
...               ...          ...          ...          ...          ...   
134a       857.995929  1312.907512  2229.968554  2277.015315  1647.022071   
134b      3333.697399  1279.477659   969.514849   703.240582  1470.404798   
135a      1259.744664  2092.475610   973.962262   879.734095  3540.418662   
135b      3534.544299  2687.819309  2057.639512  1272.078700  1946.622239   
136a       603.189831  1866.069010  2143.160409  1915.643888  3073.185281   

                                                              
paradigm                                                      
channel           AF4          Fp2           Fz           Cz  
eeg_file                                                      
101a      1552.274569  1118.361656  2046.250029  4111.674289  
101b      2404.113751  1296.808036  2214.559418  1576.898643  
102a       709.788804  3294.746439  1030.659485   648.467398  
102b       927.441687  2145.200300   721.698948   739.303826  
103a      6677.814226  6812.380543  8331.428201  5447.032441  
...       

In [11]:
df.columns = ['_'.join(str(s).strip() for s in col if s) for col in df.columns]
df

mean_2_Fp1  mean_2_AF3  mean_2_F7  mean_2_F3  mean_2_FC1  \
eeg_file                                                             
101a        3.981499   11.639081 -18.811622  18.343454   10.023632   
101b       -9.964857   -7.810340  19.733811   3.661548   14.292444   
102a        2.390371  -17.843979  -3.338771   7.536740  -10.998419   
102b        7.074118   23.187111  -9.459183  25.835532   18.345802   
103a      -18.065883  -17.785199 -12.858838  -8.709094    9.764843   
...              ...         ...        ...        ...         ...   
134a       25.305783   39.678430  29.960605  22.644373    2.972337   
134b       -9.407622   -9.174790 -29.506209 -12.091466   -3.002780   
135a      -24.276921  -15.623758 -40.422530  -1.687877   11.960549   
135b      -18.316388   -1.091161 -33.190223  -7.661494   19.655141   
136a      -23.800958    4.628651 -71.338129 -65.563532  -63.851880   

          mean_2_FC5  mean_2_T7  mean_2_C3  mean_2_CP1  mean_2_CP5  ...  \
eeg_file                                                            ...   
101a       -4.024143 -13.999364 -17.671889  -29.638338  -20.809440  ...   
101b       32.492531  34.867429  41.204902   33.612812   31.951770  ...   
102a       18.220947  16.625307  -4.156407  -17.935160   -6.441905  ...   
102b       34.434200  34.885866  22.527005   37.353435   30.657794  ...   
103a       -1.953743  -2.150446  11.090374    0.289517    2.440453  ...   
...              ...        ...        ...         ...         ...  ...   
134a       40.967793  15.140849  -5.808729    2.409057    2.371273  ...   
134b      -12.201141 -28.593497   9.314769  -14.475088  -10.563468  ...   
135a      -12.416261   1.713572  26.404282    4.149861    8.584280  ...   
135b        1.925744   8.144818   4.500359   -0.237321  -28.335054  ...   
136a      -47.764771   1.639489 -45.163899  -48.791706  -30.078101  ...   

            var_11_C4    var_11_T8   var_11_FC6   var_11_FC2    var_11_F4  \
eeg_file                                                                    
101a      1250.903147  1048.163775   829.777806  1753.590043  1872.420561   
101b       638.018139   265.097401   829.590332   841.305561   998.880934   
102a       968.669479  1071.194015  1716.894816   715.093446  1024.329442   
102b       525.391609  1310.806211  1220.034698   699.721095   640.816934   
103a      3465.824136  4562.069804  3921.895014  4897.122661  6606.174032   
...               ...          ...          ...          ...          ...   
134a      1553.391866   857.995929  1312.907512  2229.968554  2277.015315   
134b      1413.633013  3333.697399  1279.477659   969.514849   703.240582   
135a      1127.357596  1259.744664  2092.475610   973.962262   879.734095   
135b      3136.622465  3534.544299  2687.819309  2057.639512  1272.078700   
136a       951.714398   603.189831  1866.069010  2143.160409  1915.643888   

            var_11_F8   var_11_AF4   var_11_Fp2    var_11_Fz    var_11_Cz  
eeg_file                                                                   
101a      1177.183239  1552.274569  1118.361656  2046.250029  4111.674289  
101b       927.018252  2404.113751  1296.808036  2214.559418  1576.898643  
102a       481.196607   709.788804  3294.746439  1030.659485   648.467398  
102b      1312.299428   927.441687  2145.200300   721.698948   739.303826  
103a      5596.697825  6677.814226  6812.380543  8331.428201  5447.032441  
...               ...          ...          ...          ...          ...  
134a      1647.022071  1327.272928  1265.103434  2983.075714  1931.228795  
134b      1470.404798   347.950396   397.112871  7916.357558  1439.433341  
135a      3540.418662   651.492600   586.480988   833.189658  1075.406217  
135b      1946.622239   984.623436   595.782777  1429.273768  3654.095711  
136a      3073.185281  4915.869612  2786.661985  3720.272119  3102.269122  

[62 rows x 640 columns]

In [12]:
df.reset_index(inplace=True)
df

eeg_file  mean_2_Fp1  mean_2_AF3  mean_2_F7  mean_2_F3  mean_2_FC1  \
0      101a    3.981499   11.639081 -18.811622  18.343454   10.023632   
1      101b   -9.964857   -7.810340  19.733811   3.661548   14.292444   
2      102a    2.390371  -17.843979  -3.338771   7.536740  -10.998419   
3      102b    7.074118   23.187111  -9.459183  25.835532   18.345802   
4      103a  -18.065883  -17.785199 -12.858838  -8.709094    9.764843   
..      ...         ...         ...        ...        ...         ...   
57     134a   25.305783   39.678430  29.960605  22.644373    2.972337   
58     134b   -9.407622   -9.174790 -29.506209 -12.091466   -3.002780   
59     135a  -24.276921  -15.623758 -40.422530  -1.687877   11.960549   
60     135b  -18.316388   -1.091161 -33.190223  -7.661494   19.655141   
61     136a  -23.800958    4.628651 -71.338129 -65.563532  -63.851880   

    mean_2_FC5  mean_2_T7  mean_2_C3  mean_2_CP1  ...    var_11_C4  \
0    -4.024143 -13.999364 -17.671889  -29.638338  ...  1250.903147   
1    32.492531  34.867429  41.204902   33.612812  ...   638.018139   
2    18.220947  16.625307  -4.156407  -17.935160  ...   968.669479   
3    34.434200  34.885866  22.527005   37.353435  ...   525.391609   
4    -1.953743  -2.150446  11.090374    0.289517  ...  3465.824136   
..         ...        ...        ...         ...  ...          ...   
57   40.967793  15.140849  -5.808729    2.409057  ...  1553.391866   
58  -12.201141 -28.593497   9.314769  -14.475088  ...  1413.633013   
59  -12.416261   1.713572  26.404282    4.149861  ...  1127.357596   
60    1.925744   8.144818   4.500359   -0.237321  ...  3136.622465   
61  -47.764771   1.639489 -45.163899  -48.791706  ...   951.714398   

      var_11_T8   var_11_FC6   var_11_FC2    var_11_F4    var_11_F8  \
0   1048.163775   829.777806  1753.590043  1872.420561  1177.183239   
1    265.097401   829.590332   841.305561   998.880934   927.018252   
2   1071.194015  1716.894816   715.093446  1024.329442   481.196607   
3   1310.806211  1220.034698   699.721095   640.816934  1312.299428   
4   4562.069804  3921.895014  4897.122661  6606.174032  5596.697825   
..          ...          ...          ...          ...          ...   
57   857.995929  1312.907512  2229.968554  2277.015315  1647.022071   
58  3333.697399  1279.477659   969.514849   703.240582  1470.404798   
59  1259.744664  2092.475610   973.962262   879.734095  3540.418662   
60  3534.544299  2687.819309  2057.639512  1272.078700  1946.622239   
61   603.189831  1866.069010  2143.160409  1915.643888  3073.185281   

     var_11_AF4   var_11_Fp2    var_11_Fz    var_11_Cz  
0   1552.274569  1118.361656  2046.250029  4111.674289  
1   2404.113751  1296.808036  2214.559418  1576.898643  
2    709.788804  3294.746439  1030.659485   648.467398  
3    927.441687  2145.200300   721.698948   739.303826  
4   6677.814226  6812.380543  8331.428201  5447.032441  
..          ...          ...          ...          ...  
57  1327.272928  1265.103434  2983.075714  1931.228795  
58   347.950396   397.112871  7916.357558  1439.433341  
59   651.492600   586.480988   833.189658  1075.406217  
60   984.623436   595.782777  1429.273768  3654.095711  
61  4915.869612  2786.661985  3720.272119  3102.269122  

[62 rows x 641 columns]

## Merge and safe dataframe

We still need to merge some of the metadata into the dataframe, so we have the information of the age, gender and label of the participant. 

In [15]:
df = pd.merge(df, metadata, on='eeg_file')

In [16]:
pd.set_option('display.max_columns', None)

In [17]:
df

eeg_file  mean_2_Fp1  mean_2_AF3  mean_2_F7  mean_2_F3  mean_2_FC1  \
0      101a    3.981499   11.639081 -18.811622  18.343454   10.023632   
1      101b   -9.964857   -7.810340  19.733811   3.661548   14.292444   
2      102a    2.390371  -17.843979  -3.338771   7.536740  -10.998419   
3      102b    7.074118   23.187111  -9.459183  25.835532   18.345802   
4      103a  -18.065883  -17.785199 -12.858838  -8.709094    9.764843   
..      ...         ...         ...        ...        ...         ...   
57     134a   25.305783   39.678430  29.960605  22.644373    2.972337   
58     134b   -9.407622   -9.174790 -29.506209 -12.091466   -3.002780   
59     135a  -24.276921  -15.623758 -40.422530  -1.687877   11.960549   
60     135b  -18.316388   -1.091161 -33.190223  -7.661494   19.655141   
61     136a  -23.800958    4.628651 -71.338129 -65.563532  -63.851880   

    mean_2_FC5  mean_2_T7  mean_2_C3  mean_2_CP1  mean_2_CP5   mean_2_P7  \
0    -4.024143 -13.999364 -17.671889  -29.638338  -20.809440   -1.649639   
1    32.492531  34.867429  41.204902   33.612812   31.951770   20.079690   
2    18.220947  16.625307  -4.156407  -17.935160   -6.441905  121.890858   
3    34.434200  34.885866  22.527005   37.353435   30.657794    9.227958   
4    -1.953743  -2.150446  11.090374    0.289517    2.440453  -25.290242   
..         ...        ...        ...         ...         ...         ...   
57   40.967793  15.140849  -5.808729    2.409057    2.371273  -16.124015   
58  -12.201141 -28.593497   9.314769  -14.475088  -10.563468   11.710869   
59  -12.416261   1.713572  26.404282    4.149861    8.584280   -1.089667   
60    1.925744   8.144818   4.500359   -0.237321  -28.335054  -39.632992   
61  -47.764771   1.639489 -45.163899  -48.791706  -30.078101  -42.668600   

    mean_2_P3  mean_2_Pz  mean_2_PO3  mean_2_O1  mean_2_Oz  mean_2_O2  \
0  -32.836182 -25.089137  -14.058208  -6.716840  -2.735177  15.959148   
1   33.004342  47.106947   16.047153  18.948667  13.488968  41.676226   
2  -20.959377 -30.109576  -36.423459 -48.222797 -49.270759 -47.487626   
3   -0.423742  21.558211    2.807007  -6.300240 -12.444106 -16.628030   
4   -2.225579 -24.342874  -22.344942 -69.754325 -37.933675 -34.506890   
..        ...        ...         ...        ...        ...        ...   
57  -8.495528 -39.770122  -42.275741 -20.217516 -20.879863 -25.131012   
58   4.583763 -10.857757  -11.240576  -0.825501 -13.094532 -32.373004   
59  12.611668   0.625841   30.848250 -34.937885 -11.287057   1.069349   
60 -35.763394 -12.608468  -49.871970 -79.451735 -75.950539 -78.624720   
61 -15.520146  -2.122818   -5.367420 -26.367811 -59.295862 -32.404834   

    mean_2_PO4   mean_2_P4  mean_2_P8  mean_2_CP6  mean_2_CP2  mean_2_C4  \
0     9.684461   -7.813129  26.970295  -28.421906   -9.930234 -20.475391   
1    43.427540   40.873165  10.343188   18.746008   33.536461   9.225375   
2   -42.194763  -21.107573 -53.294169   -3.462877  -12.826861  -1.850998   
3    11.745936    7.598404  -1.602566    6.569263   17.644797   2.964421   
4   -22.397578  -16.122848 -35.664857  -27.412158  -13.155575 -20.610507   
..         ...         ...        ...         ...         ...        ...   
57  -36.023092   11.689667 -24.061500    2.723040   -7.686434  26.249341   
58  -31.806399  -15.637341 -23.601354  -67.989346   -9.797396 -20.846380   
59   -1.175713  -12.901503  46.004149    9.475255   13.079115  19.546301   
60  -61.443854  -47.916057 -52.305876  -21.913503    1.194803  -3.203793   
61  -43.416092 -161.176835 -16.808039  -42.000250  -32.033178 -72.153893   

    mean_2_T8  mean_2_FC6  mean_2_FC2  mean_2_F4  mean_2_F8  mean_2_AF4  \
0  -16.453635  -15.024620    2.507455  17.438440  -6.527760  -23.084612   
1  -36.343262  -16.401943   12.715096 -19.174968 -13.558111  -23.307298   
2    5.835483   12.674298   -2.258531  -6.508343   8.869047  -12.068314   
3  -11.866630    4.853979   16.785368  -2.905882  -6.796042   -4.401430   
4   -4.306012  -16.590048  -11.562932 -19.827131

Drop some unnecessary columns. 

In [18]:
df = df.drop(['eeg_file','age_months_days',
       'dyslexic_parent', 'eeg_path', 'path_epoch',
       'epoch_file'], axis =1)

Every participant has now two rows, one for each test. We now want a single row for each participant, since the participant already has experience with the test and therefore the test at time b might differ from the test atime a. To avoid bias in the data, both tests will be appended to the participant into one row. 

In [19]:
a = df.loc[df['test'] == 'a']
b = df.loc[df['test'] == 'b']
a = a.drop(['test'],axis=1)
b = b.drop(['test','sex','age_months','Group_AccToParents'], axis=1)

In [30]:
df = pd.merge(a, b, on='ParticipantID',suffixes=("_a", "_b"))
df = df.drop(['ParticipantID'],axis=1)

In [31]:
df['sex'] = np.where((df['sex']=='m'), 1,0)
df['Group_AccToParents'] = np.where((df['Group_AccToParents']=='At risk'), 1,0)

In [32]:
df.to_csv('df_avg_mmr.csv', index=False) # safe dataframe

In [33]:
first = df.pop('Group_AccToParents')
df.insert(0, 'Group_AccToParents', first)

In [34]:
df

Group_AccToParents  mean_2_Fp1_a  mean_2_AF3_a  mean_2_F7_a  mean_2_F3_a  \
0                    1      3.981499     11.639081   -18.811622    18.343454   
1                    0      2.390371    -17.843979    -3.338771     7.536740   
2                    1    -18.065883    -17.785199   -12.858838    -8.709094   
3                    1     52.196651     51.457712    22.673943    32.572107   
4                    1   -841.737108   -801.240011  -879.743229  -923.354318   
5                    1      1.179806      6.366317   -22.585827   -16.469787   
6                    1   -104.473044   -114.661477  -115.992143  -104.786412   
7                    1    -36.590509    -35.888334   -32.303728   -41.009655   
8                    1    -13.833605     -3.938048    11.836307   -27.299734   
9                    0     32.232969     33.826705    38.582741    10.956048   
10                   1     29.180499     51.305511    33.684065    77.669493   
11                   1     22.242199     25.520269    39.872521    19.348655   
12                   1    -31.569763    -36.870816   -25.511910   -23.361550   
13                   0     38.784592     29.259179    26.296711    40.195044   
14                   0    -14.796851    -18.233052   -11.778195    17.131061   
15                   0    -29.402686    -38.180667   -37.993310   -30.529308   
16                   1     23.029027     20.641544    32.681382    16.101782   
17                   1      3.911541      0.752915   -12.625158    -4.708878   
18                   0      8.177599     12.867812     9.355106     7.345832   
19                   0      7.835409     12.081674     5.621291     7.866729   
20                   1     -5.134811     -2.956571    -3.854928    -0.702477   
21                   1    -30.657831    -33.416280   -12.204762   -33.585350   
22                   1    -21.874360    -18.444312   -18.145958   -18.062886   
23                   0    -71.310520    -66.972585   -63.007506   -71.390916   
24                   0      3.991304      0.285612     6.564856    -4.572449   
25                   0     -8.640994     -7.658863     2.142351   -13.315125   
26                   0     25.305783     39.678430    29.960605    22.644373   
27                   0    -24.276921    -15.623758   -40.422530    -1.687877   

    mean_2_FC1_a  mean_2_FC5_a  mean_2_T7_a  mean_2_C3_a  mean_2_CP1_a  \
0      10.023632     -4.024143   -13.999364   -17.671889    -29.638338   
1     -10.998419     18.220947    16.625307    -4.156407    -17.935160   
2       9.764843     -1.953743    -2.150446    11.090374      0.289517   
3       5.180163     18.782386    20.845702     7.723524      5.208093   
4    -801.476465   -847.688256  -737.339387  -853.147914   -732.422316   
5     -26.659719    -20.820073   -44.714848    -5.861646     -4.621675   
6     -97.066618   -104.369716  -116.949484  -105.987364    -99.901829   
7     -39.813567    -35.966233   -32.699715   -45.066325    -43.378386   
8      -8.398938   -128.276705    25.861200    -4.607624    -26.808643   
9      42.392605     35.946838    31.716506    53.214490     52.874939   
10     33.498453     42.805475    17.245443    28.664506      9.766044   
11    162.051226     22.990998    -6.394020    15.786654     29.528279   
12      1.237653    -14.786099    -5.313720    -7.251753    -12.386793   
13     44.741321     13.358658    22.685613    22.591467     38.658071   
14    -14.355069    -10.804053   -19.245607    -7.429078      9.504616   
15    -49.216338    -33.449331   -29.320461   -42.788105    -34.203085   
16     10.662650     22.661835    17.816750     9.762403      5.115609   
17      0.479959     -5.980866   -17.839059    -6.356484     23.617119   
18     21.950842      4.130464     9.176780    16.340609    -19.439242   
19      1.653053     13.897673    16.810535    13.933469     13.796412   
20    -19.436837    -14.340993    -3.633134   -25.470879    -31.181739   
21    -32.309440    -54.785107   -51.109776   -81.94143

In [35]:
df[(np.abs(stats.zscore(df)) < 5).all(axis=1)] # z score 

Group_AccToParents  mean_2_Fp1_a  mean_2_AF3_a  mean_2_F7_a  mean_2_F3_a  \
0                    1      3.981499     11.639081   -18.811622    18.343454   
1                    0      2.390371    -17.843979    -3.338771     7.536740   
5                    1      1.179806      6.366317   -22.585827   -16.469787   
7                    1    -36.590509    -35.888334   -32.303728   -41.009655   
8                    1    -13.833605     -3.938048    11.836307   -27.299734   
10                   1     29.180499     51.305511    33.684065    77.669493   
11                   1     22.242199     25.520269    39.872521    19.348655   
13                   0     38.784592     29.259179    26.296711    40.195044   
15                   0    -29.402686    -38.180667   -37.993310   -30.529308   
17                   1      3.911541      0.752915   -12.625158    -4.708878   
18                   0      8.177599     12.867812     9.355106     7.345832   
19                   0      7.835409     12.081674     5.621291     7.866729   
20                   1     -5.134811     -2.956571    -3.854928    -0.702477   
21                   1    -30.657831    -33.416280   -12.204762   -33.585350   
22                   1    -21.874360    -18.444312   -18.145958   -18.062886   
23                   0    -71.310520    -66.972585   -63.007506   -71.390916   
26                   0     25.305783     39.678430    29.960605    22.644373   
27                   0    -24.276921    -15.623758   -40.422530    -1.687877   

    mean_2_FC1_a  mean_2_FC5_a  mean_2_T7_a  mean_2_C3_a  mean_2_CP1_a  \
0      10.023632     -4.024143   -13.999364   -17.671889    -29.638338   
1     -10.998419     18.220947    16.625307    -4.156407    -17.935160   
5     -26.659719    -20.820073   -44.714848    -5.861646     -4.621675   
7     -39.813567    -35.966233   -32.699715   -45.066325    -43.378386   
8      -8.398938   -128.276705    25.861200    -4.607624    -26.808643   
10     33.498453     42.805475    17.245443    28.664506      9.766044   
11    162.051226     22.990998    -6.394020    15.786654     29.528279   
13     44.741321     13.358658    22.685613    22.591467     38.658071   
15    -49.216338    -33.449331   -29.320461   -42.788105    -34.203085   
17      0.479959     -5.980866   -17.839059    -6.356484     23.617119   
18     21.950842      4.130464     9.176780    16.340609    -19.439242   
19      1.653053     13.897673    16.810535    13.933469     13.796412   
20    -19.436837    -14.340993    -3.633134   -25.470879    -31.181739   
21    -32.309440    -54.785107   -51.109776   -81.941431    -61.475358   
22    -15.186207     -3.818178   -26.788042    -2.862869     -1.468484   
23    -42.760408    -32.995920   -14.444756   -11.680793    -37.618819   
26      2.972337     40.967793    15.140849    -5.808729      2.409057   
27     11.960549    -12.416261     1.713572    26.404282      4.149861   

    mean_2_CP5_a  mean_2_P7_a  mean_2_P3_a  mean_2_Pz_a  mean_2_PO3_a  \
0     -20.809440    -1.649639   -32.836182   -25.089137    -14.058208   
1      -6.441905   121.890858   -20.959377   -30.109576    -36.423459   
5     -22.095876    -4.973222    10.601638    -2.569269     22.411115   
7     -42.693242   -23.771905   -28.145015   -32.802494    -16.881781   
8      30.578071    29.760648   -14.907903   -39.925093    -24.510217   
10     13.157550     6.477815    10.973759    -4.999458     25.430333   
11     -3.413319   -12.325779    16.070734    43.427855     17.198112   
13     19.583421    31.807528    46.864166    46.879344     68.636992   
15    -24.468675    -0.316995    14.242161    -2.450856     51.658833   
17    -11.180628    13.052187   -59.838674     2.028601      6.131865   
18     11.323364     9.150423     3.462794     8.307030      3.208542   
19     18.152513     9.756002    20.693139    -6.042663     13.526793   
20    -23.024682   -28.522019   -38.005064   -39.396461    -24.370834   
21    -69.318418    -7.511521   -57.445755   -36.09974

In [78]:
from sklearn.decomposition import PCA

X = df.drop('Group_AccToParents',1)
y = df['Group_AccToParents']

In [79]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=0)

In [80]:
pca = PCA(n_components=1)
X_train = pca.fit_transform(X_train)
X_test = pca.transform(X_test)

In [81]:
explained_variance = pca.explained_variance_ratio_

In [82]:
explained_variance

array([0.99725155])

In [83]:
from sklearn.ensemble import RandomForestClassifier

classifier = RandomForestClassifier(max_depth=2, random_state=0)
classifier.fit(X_train, y_train)

# Predicting the Test set results
y_pred = classifier.predict(X_test)

In [84]:
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score

cm = confusion_matrix(y_test, y_pred)
print(cm)
print(accuracy_score(y_test, y_pred))

[[0 1]
 [0 5]]
0.8333333333333334


In [86]:
X.shape

(28, 1282)